In [11]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import os
from datetime import datetime

# Define file paths
base_path = r"C:\Users\patri\OneDrive\Dokumenty\bakalarka\USECASE1_tepelne_cerpadla\data\sarze_5\teplota"
meteo_file = os.path.join(base_path, "gw1100a_outdoor_temperature.csv")
tc_file = os.path.join(base_path, "xcc_venkovni_teplota_nefiltrovana.csv")

# Load data
try:
    # Load meteostation data
    df_meteo = pd.read_csv(meteo_file, header=None, names=['time', 'temperature'])
    # Fix: Skip the header row if it exists and use ISO8601 format for parsing dates
    if df_meteo['time'][0] == 'time':
        df_meteo = df_meteo.iloc[1:].reset_index(drop=True)
    df_meteo['time'] = pd.to_datetime(df_meteo['time'], format='ISO8601')
    
    # Load heat pump data
    df_tc = pd.read_csv(tc_file, header=None, names=['time', 'temperature'])
    # Fix: Skip the header row if it exists
    if df_tc['time'][0] == 'time':
        df_tc = df_tc.iloc[1:].reset_index(drop=True)
    df_tc['time'] = pd.to_datetime(df_tc['time'], format='ISO8601')
    # Create plot
    fig = make_subplots(specs=[[{"secondary_y": False}]])
    
    # Add traces
    fig.add_trace(
        go.Scatter(
            x=df_meteo['time'], 
            y=df_meteo['temperature'], 
            name="Venkovní teplota naměřená meteostanicí",
            line=dict(color='red', width=2)
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=df_tc['time'], 
            y=df_tc['temperature'], 
            name="Venkovní teplota naměřená tepelnými čerpadly",
            line=dict(color='brown', width=2)
        )
    )
    
    # Set y-axis to linear scale to ensure normal distribution display
    fig.update_yaxes(type='linear')
    
    # Update layout
    fig.update_layout(
        title="Porovnání venkovních teplot",
        xaxis_title="Čas",
        yaxis_title="Teplota (°C)",
        legend_title="Zdroj dat",
        hovermode="x unified",
        template="plotly_white"
    )
    
    # Add range slider
    fig.update_layout(
        xaxis=dict(
            rangeselector=dict(
                buttons=list([
                    dict(count=1, label="1d", step="day", stepmode="backward"),
                    dict(count=7, label="1w", step="day", stepmode="backward"),
                    dict(step="all")
                ])
            ),
            rangeslider=dict(visible=True),
            type="date"
        ),
        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=-1.2,
            xanchor="center",
            x=0.5
        )
    )
    # Show the plot
    fig.show()
    
except FileNotFoundError as e:
    print(f"Error: {e}")
    print("Please check if the file paths are correct.")
except Exception as e:
    print(f"An unexpected error occurred: {e}")
